















<img src="ALMA.png" align="center"/>
<hr style="border:2px solid darkblue"> </hr>

<div align="center">
<font color='darkblue'>
<h1>ALMA Science Archive</h1> 
<h2>Jupyter Notebooks</h2>
</font>
</div>


<hr style="border:2px solid darkblue"> </hr>



This page contains Jupyter Notebooks to programatically access the ALMA Science Archive. The notebooks interact through Virtual Observatory standards with [ALMA's ObsCore Table Access Protocol (TAP) service](https://almascience.org/tap).

Queries in [TAP](http://www.ivoa.net/documents/TAP/) are written in the SQL-like Astronomical Data Query Language ([ADQL](https://www.ivoa.net/documents/latest/ADQL.html)). ADQL queries include spatial queries as well as operations on other properties/columns of the database. This also allows the user detailed control over the returned columns.

In these Jupyter notebook we will exemplify some of the most common queries. For this we will be using the astropy affiliated [PyVO client](https://pyvo.readthedocs.io), which is interoperable with other valid TAP services from other observatories.

 <div align="center">
<font color='darkblue'>
    
<h2> Table of Contents </h2>

<hr style="border:2px solid darkblue"> </hr>

<a href="#Installation"><h3> 0. Installation</h3> </a>

<a href="nb1_ALMA_Query_one_source.ipynb"><h3> 1. Query one source</h3> </a>

<a href="nb2_ALMA_Query_public_catalogue.ipynb"><h3> 2. Query a catalogue of sources</h3></a>

 <a href="nb3_ALMA_Query_by_proposal_or_publisher_id.ipynb"><h3> 3. Query by proposal and IDs</h3> </a>

 <a href="nb4_ALMA_Query_by_science_keyword.ipynb"><h3> 4. Query by science keyword</h3></a>

 <a href="nb5_ALMA_Query_by_spatial_resolution.ipynb"><h3> 5. Query by spatial resolution</h3></a>

 <a href="nb6_ALMA_Query_by_frequency.ipynb"><h3> 6. Query by covered frequency range</h3></a>

 <a href="nb7_ALMA_Query_by_sensitivity.ipynb"><h3> 7. Query by Sensitivity</h3> </a>

 <a href="nb8_ALMA_Query_using_astroquery.ipynb"><h3> 8. Query using Astroquery.ALMA</h3></a>

<a href="nb9_ALMA_Download_data.ipynb"><h3> 9. Download data after query</h3></a>
</font>
</div>


<hr style="border:2px solid darkblue"> </hr>

<font color='darkblue'>
<a id='Installation'></a>    
<h2> 0. Installation </h2>



Install the required software with 
```bash
pip3 install jupyterlab matplotlib pandas sklearn
pip3 install --upgrade --pre astroquery
```

download the Jupyter Notebooks
```bash
wget https://almascience.org/alma-data/archive/archive-notebooks/alma-science-archive-notebooks.tgz -O - | tar -xz
cd alma-science-archive-notebooks
```
and start the notebook server
```bash
jupyter-lab
```
You can modify the code in the cells and run each cell with "Shift+Enter". An introduction to Jupyter Notebooks [can be found here](https://jupyter-notebook.readthedocs.io/en/stable/notebook.html).

<br />

#### Troubleshooting

Python 3.6 users, run: pip3 --upgrade astropy==4.1

If you experience problems with these notebooks, please contact us through the [ALMA Helpdesk](https://help.almascience.org/).

<hr style="border:2px solid darkblue">

Throughout the notebooks we will access the  [ALMA ObsCore TAP service](https://almascience.org/tap/) using:

In [1]:
import pyvo
import pandas as pd

service = pyvo.dal.TAPService("https://almascience.eso.org/tap")      # for the EU ALMA TAP service

# service = pyvo.dal.TAPService("https://almascience.nao.ac.jp/tap")  # for the EA ALMA TAP service
# service = pyvo.dal.TAPService("https://almascience.nrao.edu/tap")   # for the NA ALMA TAP service

Here some examples of the use of ADQL:

## Example 0a: Query by coordinate and request the entire result table

Find all ALMA observations where the footprint of the observation (stored in the VO column 's_region') intersects with our search circle where RA, Dec and the search radius are given in decimal degrees:

In [2]:
query = f"""
        SELECT *  
        FROM ivoa.obscore 
        WHERE INTERSECTS(CIRCLE('ICRS',201.365063,-43.019112,0.006),s_region)=1  
        """

result = service.search(query)
output = result.to_table().to_pandas()

The output has been directly converted into a pandas dataframe. For simplicity, we only display the first 5 rows.

In [3]:
pd.set_option('display.max_columns', None)
output.head(5)

access_url access_format  \
0  http://almascience.org/aq?member_ous_id=uid://...     text/html   
1  http://almascience.org/aq?member_ous_id=uid://...     text/html   
2  http://almascience.org/aq?member_ous_id=uid://...     text/html   
3  http://almascience.org/aq?member_ous_id=uid://...     text/html   
4  http://almascience.org/aq?member_ous_id=uid://...     text/html   

       proposal_id data_rights  gal_longitude  gal_latitude  \
0  2011.0.00008.SV      Public     309.512363     19.416239   
1  2011.0.00008.SV      Public     309.512363     19.416239   
2  2011.0.00008.SV      Public     309.512363     19.416239   
3  2011.0.00008.SV      Public     309.512363     19.416239   
4   2011.0.00010.S      Public     309.515914     19.417224   

              obs_publisher_did obs_collection facility_name instrument_name  \
0  ADS/JAO.ALMA#2011.0.00008.SV           ALMA           JAO            ALMA   
1  ADS/JAO.ALMA#2011.0.00008.SV           ALMA           JAO            ALMA   
2  ADS/JAO.ALMA#2011.0.00008.SV           ALMA           JAO            ALMA   
3  ADS/JAO.ALMA#2011.0.00008.SV           ALMA           JAO            ALMA   
4   ADS/JAO.ALMA#2011.0.00010.S           ALMA           JAO            ALMA   

                    obs_id dataproduct_type  calib_level  target_name  \
0  uid://A002/X259150/X157             cube            2  Centaurus A   
1  uid://A002/X259150/X157             cube            2  Centaurus A   
2  uid://A002/X259150/X157             cube            2  Centaurus A   
3  uid://A002/X259150/X157             cube            2  Centaurus A   
4  uid://A002/X327408/X217             cube            2         CenA   

         s_ra      s_dec     s_fov  \
0  201.360719 -43.020553  0.058089   
1  201.360719 -43.020553  0.058089   
2  201.360719 -43.020553  0.058089   
3  201.360719 -43.020553  0.058089   
4  201.365063 -43.019112  0.007385   

                                            s_region  s_resolution  \
0  Polygon ICRS 201.401254 -43.032096 201.401354 ...      1.023315   
1  Polygon ICRS 201.401254 -43.032096 201.401354 ...      1.023315   
2  Polygon ICRS 201.401254 -43.032096 201.401354 ...      1.023315   
3  Polygon ICRS 201.401254 -43.032096 201.401354 ...      1.023315   
4         Circle ICRS 201.365063 -43.019112 0.003692      1.330912   

          t_min         t_max  t_exptime  t_resolution    em_min    em_max  \
0  55784.795689  55785.043473    344.261       344.261  0.001221  0.001231   
1  55784.795689  55785.043473    344.261       344.261  0.001212  0.001221   
2  55784.795689  55785.043473    344.261       344.261  0.001297  0.001308   
3  55784.795689  55785.043473    344.261       344.261  0.001287  0.001297   
4  55950.253573  55950.305961   1512.000      1512.000  0.001360  0.001366   

   em_res_power pol_states                                o_ucd band_list  \
0  251315.70776    /XX/YY/  phot.flux.density;phys.polarization         6   
1  253235.70776    /XX/YY/  phot.flux.density;phys.polarization         6   
2  236599.53752    /XX/YY/  phot.flux.density;phys.polarization         6   
3  238519.53752    /XX/YY/  phot.flux.density;phys.polarization         6   
4  451534.98200    /XX/YY/  phot.flux.density;phys.polarization         6   

   em_resolution                                            authors  \
0     306.959997  Azeez, Jazeel H.; Abidin, Zamri Z.; Hwang, C. ...   
1     306.959997  Azeez, Jazeel H.; Abidin, Zamri Z.; Hwang, C. ...   
2     306.959997  Azeez, Jazeel H.; Abidin, Zamri Z.; Hwang, C. ...   
3     306.959997  Azeez, Jazeel H.; Abidin, Zamri Z.; Hwang, C. ...   
4     614.023326  McCoy, Mark; Ott, Jürgen; Meier, David S.; Mul...   

                                        pub_abstract  publication_year  \
0  Centaurus A, with its gas-rich elliptical host...              2014   
1  Centaurus A, with its gas-rich elliptical host...              2014   
2  Centaurus A, with its gas-rich elliptical host...              2014   
3  Centaurus A, w

The ALMA TAP table contains 63 columns with the following column names and units:

In [4]:
print(*sorted([f"{fieldname:28s} {result.getdesc(fieldname).unit if result.getdesc(fieldname).unit else ''}" for fieldname in result.fieldnames]), sep='\n')

access_format                
access_url                   
antenna_arrays               
asdm_uid                     
authors                      
band_list                    
bandwidth                    GHz
bib_reference                
calib_level                  
cont_sensitivity_bandwidth   mJy/beam
data_rights                  
dataproduct_type             
em_max                       m
em_min                       m
em_res_power                 
em_resolution                m
facility_name                
first_author                 
frequency                    GHz
frequency_support            GHz
gal_latitude                 deg
gal_longitude                deg
group_ous_uid                
instrument_name              
is_mosaic                    
lastModified                 
member_ous_uid               
o_ucd                        
obs_collection               
obs_creator_name             
obs_id                       
obs_publisher_did            
obs_release_da

## Example 0b: Query by coordinate and request only few columns
The query returns all ALMA observations where the footprint (s_region) intersects with the search circle specified by RA, Dec and the search radius, all in decimal degrees. Compared to the example above, the result table has now a much smaller width as only the target name, RA and Dec have been requested.

In [5]:
query = f"""   
        SELECT target_name, s_ra, s_dec   
        FROM ivoa.obscore   
        WHERE INTERSECTS(CIRCLE('ICRS',201.365063,-43.019112,0.006),s_region)=1
        """
output = service.search(query).to_table().to_pandas() 

In [6]:
pd.set_option('display.max_columns', None)
output.head(5)

target_name        s_ra      s_dec
0  Centaurus A  201.360719 -43.020553
1  Centaurus A  201.360719 -43.020553
2  Centaurus A  201.360719 -43.020553
3  Centaurus A  201.360719 -43.020553
4         CenA  201.365063 -43.019112